# Restaurant Supply Co. - expansion in NYC

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Analysis Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction: Business Problem <a name="introduction"></a>


The <b>'Restaurant Supply Co'</b> is a new small company hiring us on Coursera to help them with an ideal location for the first Sales Team in New York City.

<b>The Sales Team</b>, <br>
<b>main requirement</b> is to receive a list of the top Neighborhood with higher density of restaurants in New York City<br>
<b>in such way</b> that the salesmen may be located in the Neighborhood to cover most restaurants with minimum distance. <br>
<br>
<b>secondary requirement </b> <br>
Given that a salesman is able to have 40 restaurants in his portifolio, and the company wants to have 5 salesman at most. <br>
Determine how many clusters and recomend the central location for each one of them<br>
<br>
  


## Data  <a name="data"></a>


For this case, it makes sense to use the <a href=https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json> newyork_data.json </a> data available on Coursera.
<br>    
From newyork_data.json it will be used 'Borough', 'Neighborhood', 'Latitude', 'Longitude', making possible to retrieve venues from <b>Foursquare</b>. From those venues it will be selected/filtered those with one the words: restaurant, bakery, coffee, café, bar, breakfast, burger, creperie, food, gastro, hot dog, pub and steakhouse.
<br><br>
<b>The first deliverable</b> will be ready when data collection and cleanning is completed in the previous step, it means, the complete list of neighborhoods with restaurants quantity.    
<br>
<b>The secondary deliverable</b> will be obtained from the quantity of restaurants in New York City, it will be calculated the quantity of clusters by dividing the restaurants of NY by 40 * 5 (40 restaurants times 5 salesmen per Sales Team Location). With this number, obtain the k-mean and determine the center of each cluster. 
<br><br>


#### from newyork_data.json

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

import wget

#get data file from Cousera and transform in a pandas DataFrame
wget.download('https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json', 'newyork_data.json')
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
neighborhoods_data = newyork_data['features']    
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 
neighborhoods = pd.DataFrame(columns=column_names)
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

100% [............................................................................] 115774 / 115774

#### setup Foursquare credentials

In [2]:
#prepare credentials for Foursquare
CLIENT_ID = 'ALVM5DKWATEHOR43TP2DPVHDMU5CTD2QIV3SWZSU5SKBY0GR' # your Foursquare ID
CLIENT_SECRET = 'PBPMTTVA4UB2KTQOIVZXQRFNZ0WPSA1YKQRG0FJUSNH5HWB1' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value


#### function to iterate neighborhood retrieving Venues in a radius of 500 meters

In [3]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [4]:
#lets use the function above for all neighborhood of NYC
nyc_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                               latitudes=neighborhoods['Latitude'],
                               longitudes=neighborhoods['Longitude']
                              )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

## main deliverable
#### from this list of venues retrieved from Foursquare
1. use the word_set and clean undesired venues
2. attempt to main_deliverable and determine the neighborhood with most restaurants

In [5]:
word_set = set(['restaurant', 'bakery', 'coffee', 'café', 'bar', 'breakfast', 'burger', 'creperie', 'food', 'gastro', 'hot dog', 'pub', 'steakhouse'])
rows_list = []
for i, row in nyc_venues.iterrows():
    category = set(row[6].lower() .split())
    if word_set.intersection(category):    
        rows_list.append(row)
nyc_filtered = pd.DataFrame(rows_list) 

main_deliverable = nyc_filtered.groupby(['Neighborhood']).size().reset_index(name='counts')
main_deliverable = main_deliverable.sort_values(by=['counts'], ascending=False)
#this the list requested by 'Restaurant Supplier Co'
main_deliverable

Neighborhood  counts
171                Murray Hill      88
6                      Astoria      68
256            Upper West Side      65
234                 South Side      62
74                East Village      60
252                 Turtle Bay      56
201           Prospect Heights      55
179                 North Side      55
44                   Chinatown      55
264               West Village      54
244          Sunnyside Gardens      54
176                       Noho      54
112          Greenwich Village      54
39             Carroll Gardens      52
86          Financial District      52
66                    Downtown      50
138                 Lenox Hill      49
111                 Greenpoint      48
38               Carnegie Hill      48
54                 Cobble Hill      48
43                     Chelsea      47
142               Little Italy      47
88                    Flatiron      46
127            Jackson Heights      46
52                Clinton Hill      45
47                Civic Center      45
161              Midtown South      45
276                  Yorkville      45
250                    Tribeca      44
246               Sutton Place      44
21                     Belmont      43
105                   Gramercy      43
14                     Bayside      43
51                     Clinton      43
275                   Woodside      39
124              Hunters Point      38
230                       Soho      38
260         Washington Heights      38
251                 Tudor City      37
160                    Midtown      37
255            Upper East Side      37
11                   Bay Ridge      36
35                    Bushwick      36
113           Hamilton Heights      35
25                 Boerum Hill      34
95                 Fort Greene      33
32            Brooklyn Heights      33
91                    Flushing      32
75           East Williamsburg      31
144           Long Island City      31
190                 Park Slope      31
122               Hudson Yards      30
140             Lincoln Square      29
126                     Inwood      28
151             Manhattanville      28
150           Manhattan Valley      26
134                Kingsbridge      26
81                    Elmhurst      25
143                Little Neck      25
104                    Gowanus      25
243                  Sunnyside      24
202  Prospect Lefferts Gardens      24
146            Lower East Side      24
96               Fort Hamilton      23
41              Central Harlem      22
63                 Ditmas Park      22
71                 East Harlem      21
9                   Bath Beach      21
164        Morningside Heights      21
99                Fulton Ferry      20
92                     Fordham      20
216             Rockaway Beach      19
67                       Dumbo      19
209                  Rego Park      19
262              West Brighton      18
10           Battery Park City      18
163                 Mill Basin      17
208                   Red Hook      17
132                Kew Gardens      17
55               College Point      17
207                 Ravenswood      16
214                  Ridgewood      16
192                 Pelham Bay      16
22                 Bensonhurst      16
28              Brighton Beach      16
130              Jamaica Hills      15
16          Bedford Stuyvesant      15
259               Vinegar Hill      15
268               Williamsburg      15
166                Morris Park      14
135        Kingsbridge Heights      14
34                  Bulls Head      14
245                Sunset Park      14
203        Prospect Park South      14
121               Howard Beach      14
239                  Stapleton      13
78              Edgewater Park      13
82                 Eltingville      13
172                   New Dorp      13
120                  Homecrest      11
116               High  Bridge      11
12                 Bay Terrace      11
5

## second deliverable
#### determination of clusters
lets consider the fact: 40 restaurants per salesman and 5 salesman per team

In [6]:
nyc_filtered.shape

(4137, 7)

In [7]:
print ('Quantity of teams(clusters) in NYC should be {}'.format(round(4111/(40*5))))

Quantity of teams(clusters) in NYC should be 21


## Machine Learning
#### use k-means to determine cluster of each restaurant and the center of each cluster

In [8]:
# set number of clusters
kclusters = 21
# set latitude and longitude of each restaurant
nyc_grouped_clustering = nyc_filtered.drop(['Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude', 'Venue', 'Venue Category'], 1)
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(nyc_grouped_clustering)
# add clustered labels
nyc_filtered.insert(0, 'Cluster Labels', kmeans.labels_)
# add clustered location
nyc_filtered['Cluster Latitude'] = 0
nyc_filtered['Cluster Longitude'] = 0
for i, row in nyc_filtered.iterrows():
    nyc_filtered.loc[i, 'Cluster Latitude'] = kmeans.cluster_centers_[row['Cluster Labels'], 0]
    nyc_filtered.loc[i, 'Cluster Longitude'] = kmeans.cluster_centers_[row['Cluster Labels'], 1]

#### examining some clusters

In [9]:
nyc_filtered.loc[nyc_filtered['Cluster Labels'] == 0, nyc_filtered.columns[[1] + list(range(5, nyc_filtered.shape[1]))]]

Neighborhood  Venue Latitude  Venue Longitude  \
4200    Lincoln Square       40.772097       -73.982082   
4206    Lincoln Square       40.771183       -73.983325   
4210    Lincoln Square       40.771505       -73.982292   
4214    Lincoln Square       40.771029       -73.981808   
4216    Lincoln Square       40.771930       -73.981576   
4217    Lincoln Square       40.772034       -73.982170   
4220    Lincoln Square       40.771859       -73.982301   
4222    Lincoln Square       40.771735       -73.981996   
4229    Lincoln Square       40.772657       -73.981639   
4232    Lincoln Square       40.772205       -73.981177   
4239    Lincoln Square       40.775568       -73.989927   
4242    Lincoln Square       40.772918       -73.982191   
4253    Lincoln Square       40.772881       -73.989666   
4255    Lincoln Square       40.771848       -73.982776   
4257    Lincoln Square       40.771392       -73.982424   
4259    Lincoln Square       40.769690       -73.988238   
4264    Lincoln Square       40.771650       -73.982335   
4265    Lincoln Square       40.769707       -73.988041   
4267    Lincoln Square       40.776274       -73.987419   
4268    Lincoln Square       40.776728       -73.989234   
4269    Lincoln Square       40.769750       -73.988481   
4276           Clinton       40.760636       -73.994714   
4282           Clinton       40.760905       -73.994601   
4288           Clinton       40.759927       -73.995294   
4289           Clinton       40.758576       -73.993653   
4292           Clinton       40.760725       -73.998425   
4295           Clinton       40.757646       -73.997997   
4301           Clinton       40.761156       -73.998140   
4306           Clinton       40.756024       -73.996366   
4309           Clinton       40.759182       -73.995513   
4310           Clinton       40.761532       -73.994181   
4312           Clinton       40.760512       -73.998985   
4313           Clinton       40.761024       -73.994518   
4315           Clinton       40.758653       -73.993099   
4317           Clinton       40.757177       -73.993518   
4323           Clinton       40.759915       -73.992193   
4324           Clinton       40.762475       -73.997009   
4326           Clinton       40.761341       -73.994277   
4327           Clinton       40.762030       -73.993550   
4332           Clinton       40.755722       -73.994627   
4333           Clinton       40.760726       -73.997724   
4337           Clinton       40.762408       -73.996936   
4340           Clinton       40.760234       -73.990927   
4341           Clinton       40.759158       -73.992022   
4342           Clinton       40.758696       -73.993221   
4346           Clinton       40.760521       -73.994921   
4348           Clinton       40.760070       -73.990815   
4350           Clinton       40.759360       -73.991871   
4352           Clinton       40.755531       -73.994769   
4353           Clinton       40.759838       -73.991564   
4354           Clinton       40.756298       -73.993507   
4355           Clinton       40.760399       -73.990817   
4356           Clinton       40.760180       -73.991095   
4358           Clinton       40.755271       -73.998509   
4359           Clinton       40.760563       -73.991087   
4361           Clinton       40.759045       -73.994948   
4362           Clinton       40.756251       -73.991630   
4363           Clinton       40.763245       -73.994166   
4364           Clinton       40.759448       -73.995213   
4366           Clinton       40.760845       -73.990896   
4367           Clinton       40.756079       -73.994594   
4372           Clinton       40.762053       -73.993609   
4374           Clinton       40.760100       -73.991378   
4375           Clinton       40.759392       -73.991038   
4379           Midtown       40.754143       -73.983505   
4380           Midtown       40.754016       -73.981719   
4384           Midtown       40.755298       -73.980690  

In [10]:
nyc_filtered.loc[nyc_filtered['Cluster Labels'] == 1, nyc_filtered.columns[[1] + list(range(5, nyc_filtered.shape[1]))]]

Neighborhood  Venue Latitude  Venue Longitude  \
6136           Flushing       40.764852       -73.831767   
6137           Flushing       40.763658       -73.831737   
6141           Flushing       40.762083       -73.828963   
6143           Flushing       40.761083       -73.829609   
6145           Flushing       40.762316       -73.827633   
6147           Flushing       40.761195       -73.827749   
6148           Flushing       40.761794       -73.830341   
6149           Flushing       40.760839       -73.832905   
6151           Flushing       40.760649       -73.833037   
6153           Flushing       40.761294       -73.831998   
6154           Flushing       40.760532       -73.832921   
6155           Flushing       40.761012       -73.830193   
6157           Flushing       40.760675       -73.833210   
6158           Flushing       40.761574       -73.831058   
6159           Flushing       40.760663       -73.829268   
6160           Flushing       40.761039       -73.832690   
6161           Flushing       40.760985       -73.830766   
6162           Flushing       40.760765       -73.830553   
6165           Flushing       40.760285       -73.830250   
6167           Flushing       40.763890       -73.831550   
6171           Flushing       40.767200       -73.832700   
6172           Flushing       40.763804       -73.827143   
6174           Flushing       40.763645       -73.827392   
6176           Flushing       40.763641       -73.831236   
6179           Flushing       40.763196       -73.830835   
6180           Flushing       40.763672       -73.831749   
6181           Flushing       40.763669       -73.831371   
6182           Flushing       40.764603       -73.831684   
6185           Flushing       40.764006       -73.831342   
6186           Flushing       40.764145       -73.828163   
6188           Flushing       40.763081       -73.829712   
6191           Flushing       40.766580       -73.827413   
6518      College Point       40.784360       -73.845372   
6520      College Point       40.784442       -73.845817   
6522      College Point       40.782462       -73.845976   
6531      College Point       40.781346       -73.841053   
6532      College Point       40.784095       -73.845659   
6533      College Point       40.785299       -73.841422   
6536      College Point       40.781417       -73.840764   
6538      College Point       40.781349       -73.845947   
6539      College Point       40.785172       -73.841450   
6541      College Point       40.783919       -73.845523   
6543      College Point       40.785023       -73.846039   
6544      College Point       40.782986       -73.841410   
6547      College Point       40.782989       -73.845884   
6548      College Point       40.783903       -73.846654   
6552      College Point       40.781412       -73.841077   
6558      College Point       40.785960       -73.837418   
6559      College Point       40.781826       -73.847198   
6641         Auburndale       40.763338       -73.793057   
6647         Auburndale       40.757848       -73.791722   
6650         Auburndale       40.757457       -73.793444   
6652         Auburndale       40.757838       -73.789141   
6658         Auburndale       40.765486       -73.788748   
6659         Auburndale       40.758298       -73.795392   
6774  Kew Gardens Hills       40.725835       -73.821606   
6777  Kew Gardens Hills       40.724137       -73.820293   
6778  Kew Gardens Hills       40.722934       -73.819618   
6783  Kew Gardens Hills       40.725921       -73.821702   
7066         Beechhurst       40.796289       -73.806327   
7071         Beechhurst       40.792408       -73.806892   
7075         Beechhurst       40.793805       -73.807543   
7078         Beechhurst       40.793686       -73.807884   
7206        Murray Hill       40.763022       -73.815042   
7207        Murray Hill       40.763125       -73.814341   
7208        Murray Hill       40.764717       -73.8

In [11]:
nyc_filtered.loc[nyc_filtered['Cluster Labels'] == 15, nyc_filtered.columns[[1] + list(range(5, nyc_filtered.shape[1]))]]

Neighborhood  Venue Latitude  Venue Longitude  \
7632      Port Richmond       40.632528       -74.133853   
7635   Mariner's Harbor       40.631772       -74.146950   
7640         Port Ivory       40.639359       -74.171533   
7644  Castleton Corners       40.613093       -74.121809   
7645  Castleton Corners       40.613121       -74.120907   
7652  Castleton Corners       40.613106       -74.123719   
7655  Castleton Corners       40.613212       -74.123846   
7662    New Springville       40.589778       -74.164390   
7663    New Springville       40.592496       -74.162623   
7665    New Springville       40.590926       -74.164461   
7670    New Springville       40.598126       -74.162204   
7676    New Springville       40.590757       -74.164559   
7679    New Springville       40.590048       -74.165303   
7723            Oakwood       40.558553       -74.125286   
7952        Westerleigh       40.624448       -74.136816   
7953        Westerleigh       40.624640       -74.132175   
7954        Westerleigh       40.624273       -74.136416   
7956       Graniteville       40.623263       -74.149036   
7959          Arlington       40.637370       -74.162424   
8194  Heartland Village       40.589778       -74.164390   
8196  Heartland Village       40.592496       -74.162623   
8200  Heartland Village       40.592895       -74.157430   
8203            Chelsea       40.594140       -74.186735   
8210         Bloomfield       40.602161       -74.185364   
8212         Bulls Head       40.611810       -74.158749   
8213         Bulls Head       40.608315       -74.162827   
8214         Bulls Head       40.611896       -74.157533   
8217         Bulls Head       40.612195       -74.159093   
8219         Bulls Head       40.611625       -74.159182   
8222         Bulls Head       40.611972       -74.157463   
8223         Bulls Head       40.607976       -74.163452   
8236         Bulls Head       40.612673       -74.158819   
8240         Bulls Head       40.611972       -74.159805   
8244         Bulls Head       40.606826       -74.162815   
8246         Bulls Head       40.608051       -74.162487   
8248         Bulls Head       40.607778       -74.162869   
8251         Bulls Head       40.607841       -74.162981   
8257         Bulls Head       40.612605       -74.162603   
8655      Richmond Town       40.573267       -74.136584   
8657      Richmond Town       40.573073       -74.136913   
8721           Elm Park       40.634205       -74.143781   
8722           Elm Park       40.631772       -74.146950   
9747      Manor Heights       40.604350       -74.120644   
9748      Manor Heights       40.604778       -74.121160   
9758        Willowbrook       40.603764       -74.131514   
9774        Egbertville       40.575515       -74.127905   
9846    Lighthouse Hill       40.573267       -74.136584   
9848    Lighthouse Hill       40.573073       -74.136913   

            Venue Category  Cluster Latitude  Cluster Longitude  
7632        Breakfast Spot         40.605336         -74.151585  
7635    Italian Restaurant         40.605336         -74.151585  
7640                   Bar         40.605336         -74.151585  
7644    Mexican Restaurant         40.605336         -74.151585  
7645   Japanese Restaurant         40.605336         -74.151585  
7652          Burger Joint         40.605336         -74.151585  
7655                   Bar         40.605336         -74.151585  
7662            Restaurant         40.605336         -74.151585  
7663           Coffee Shop         40.605336         -74.151585  
7665    Mexican Restaurant         40.605336         -74.151585  
7670            Hookah Bar         40.605336         -74.151585  
7676    Chinese Restaurant         40.605336         -74.151585  
7679    Chinese Restaurant         40.605336         -74.151585  
7723                   Bar         40.605336         -74.151585  
7952      Sushi Restaurant         40.605336         -74.151585  
7953    Spanis

## Analysis Results and Discussion <a name="results"></a>

### Main Delivery

<b>Restaurant Supplier Co.</b>, received the list of the neighborhood with most restaurants.<br>
We at Coursera are pointing the 10 neighborhood. That represents 618 of 4111 restaurants in NYC or 15% of the total.
Murray Hill demands 2 salesman to cover the area. 

In [12]:
main_deliverable.head(10)

Neighborhood  counts
171       Murray Hill      88
6             Astoria      68
256   Upper West Side      65
234        South Side      62
74       East Village      60
252        Turtle Bay      56
201  Prospect Heights      55
179        North Side      55
44          Chinatown      55
264      West Village      54

### Secondary Delivery

Actually NYC has 4111 restaurants, which lead us to 21 Sales Teams attending the prerequisites of the instructions.
We have scientifically determined 21 center locations for each of the Sales Teams and respective restaurants for the area of responsibility. 


In [13]:
#get location of NYC
address = 'New York City, NY'
geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(nyc_filtered['Cluster Latitude'], nyc_filtered['Cluster Longitude'], nyc_filtered['Cluster Labels'], nyc_filtered['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Conclusion <a name="conclusion"></a>

Purpose of this project was to identify NYC areas high number of restaurants in order to aid stakeholders in narrowing down the search for optimal location for restaurant supplies sales. By calculating restaurant density distribution from Foursquare data we have first identified to 10 Neighbourhoods with Murray Hill at the top with 88 restaurants, and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to balance Sales Team centers, and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.


### Thanks for reading my notebook
Best Regards,<br>
Fabio Nozoy <br>
<a href=“mailto:fnozoy@yahoo.com” target=“_top”>
fnozoy@yahoo.com</a>